In [ ]:
!nvidia-smi

In [21]:
import torch
torch._dynamo.config.cache_size_limit = 64
torch._dynamo.config.suppress_errors = True
torch.set_float32_matmul_precision('high')

import ChatTTS
from IPython.display import Audio,display

## Load Models

In [11]:
chat = ChatTTS.Chat()
chat.load_models(source='local', local_path='.\ChatTTS')  

# Use force_redownload=True if the weights updated.
# chat.load_models(force_redownload=True)

# If you download the weights manually, set source='locals'.
# chat.load_models(source='local', local_path='YOUR LOCAL PATH')

INFO:ChatTTS.core:Load from local: .\ChatTTS
INFO:ChatTTS.core:use cuda:0
INFO:ChatTTS.core:vocos loaded.
INFO:ChatTTS.core:dvae loaded.
INFO:ChatTTS.core:gpt loaded.
INFO:ChatTTS.core:decoder loaded.
INFO:ChatTTS.core:tokenizer loaded.
INFO:ChatTTS.core:All initialized.


## Inference

### Batch infer

In [12]:
texts = ["Hello everyone, I'm Mu You. Today, I'd like to share an interesting TTS project with you. In just three days, the project has already reached 11.7K stars.",]*3 \
        + ["大家好，我是沐柚，今天给大家分享一个好玩的TTS项目，这个项目在短短三天内，star数量已经来到了十一点七K。"]*3     
        
wavs = chat.infer(texts)

INFO:ChatTTS.core:All initialized.
 26%|██▌       | 531/2048 [00:12<00:35, 42.51it/s]


In [13]:
Audio(wavs[2], rate=24_000, autoplay=False)

In [8]:
Audio(wavs[4], rate=24_000, autoplay=False)

In [9]:
Audio(wavs[5], rate=24_000, autoplay=False)

### Custom params

In [14]:
params_infer_code = {'prompt':'[speed_5]', 'temperature':.3}
params_refine_text = {'prompt':'[oral_2][laugh_0][break_6]'} #这里加随机的断句词
wav = chat.infer('永远不要提前焦虑，也不要提前预知烦恼，更不要被当下的情绪所消耗，那样会对你的身体造成很大的伤害，你只需要好好享受当下。车到山前必有路，关关难过关关过，揪着过去不放，不要不依不饶, 画地为牢，你要允许一切发生，调整好情绪，毕竟我们无法左右的事情太多，握不住的东西和留不住的人也太多，尽心尽力，顺其自然就好！', \
    params_refine_text=params_refine_text, params_infer_code=params_infer_code)

INFO:ChatTTS.core:All initialized.
 64%|██████▍   | 1320/2048 [00:28<00:15, 46.74it/s]


In [16]:
Audio(wav[0], rate=24_000, autoplay=False)

### fix random speaker

In [17]:
rand_spk = chat.sample_random_speaker(seed=99)  #自己修改seed的数值
params_infer_code = {'spk_emb' : rand_spk, }
params_refine_text = {'prompt':'[oral_2][laugh_0][break_6]'} #这里加随机的断句词
wav = chat.infer('不要把时间浪费在尚未发生且没有必要的人和事上，更不要在焦虑和烦恼中度过，你要把时间分给睡眠，分给书籍，分给运动，分给音乐，分给花鸟树木山川湖泊，当你开始做时间的主人，那些焦虑和烦恼自然就烟消云散了。', \
    params_refine_text=params_refine_text, params_infer_code=params_infer_code)

INFO:ChatTTS.core:All initialized.
 47%|████▋     | 959/2048 [00:20<00:23, 46.49it/s]


In [18]:
Audio(wav[0], rate=24_000, autoplay=False)

### Two stage control

In [19]:
text = "我在背后骂人说明他人品有问题 别人在背后骂我更说明他人品有问题 我骂的能是什么好东西骂我的又能是什么好东西 我就是古希腊掌管道德的神 "
chat.infer(text, refine_text_only=True)   #这里只是显示断句结果

INFO:ChatTTS.core:All initialized.
 20%|█▉        | 75/384 [00:02<00:08, 35.53it/s]


['我 在 背 后 骂 人 [uv_break] 就 说 明 他 人 品 有 问 题 [uv_break] 那 个 别 人 在 背 后 骂 我 就 更 说 明 他 人 品 有 问 题 [uv_break] 我 骂 的 能 是 什 么 好 东 西 [uv_break] 骂 我 的 又 能 是 什 么 好 东 西 [uv_break] 我 就 是 古 希 腊 掌 管 道 德 的 神']

In [20]:
text= [ "我 在 背 后 骂 人 [uv_break] 说 明 他 人 品 有 问 题 别 人 在 背 后 骂 我 更 说 明 他 人 品 有 问 题 [uv_break] 那 我 骂 的 能 是 什 么 好 东 西 [uv_break] 骂 我 的 又 能 是 什 么 好 东 西 [uv_break]  我 就 是 古 希 腊 掌 管 道 德 的 神 [laugh] "]
wav = chat.infer(text, skip_refine_text=True)   #设定不要自行断句，这里把上一行命令的断句后的文本粘贴到这里，不合适的地方进行修改。

INFO:ChatTTS.core:All initialized.
 29%|██▉       | 590/2048 [00:12<00:31, 46.53it/s]


In [ ]:
Audio(wav[0], rate=24_000, autoplay=False)

### 进阶固定音色-随机生成种子

In [22]:
texts = [
    "大家好，我是沐柚，很高兴认识大家"
    "这个项目开源不到一周，star数量已经来到了十五K。",
    "ChatTTS is optimized for dialogue-based tasks, enabling natural and expressive speech synthesis. It supports multiple speakers, facilitating interactive conversations. "
]

In [23]:
import random

seed_random = random.randint(1,1000)
print("seed", seed_random)

r = chat.sample_random_speaker(seed=seed_random)   #seed_random修改为合适的值

params_infer_code = {
    'spk_emb': r,  # add sampled speaker
    'temperature': .3,  # using custom temperature
    'top_P': 0.7,  # top P decode
    'top_K': 20,  # top K decode
}

params_refine_text = {
    'prompt': '[oral_2][laugh_0][break_6]'
}


wavs = chat.infer(texts, params_infer_code=params_infer_code,
                  params_refine_text=params_refine_text, use_decoder=True)
for i, t in enumerate(texts):
  audio = Audio(wavs[i], rate=24000, autoplay=False)
  print(i,t)
  display(audio)

INFO:ChatTTS.core:All initialized.


seed 919


 27%|██▋       | 560/2048 [00:12<00:34, 43.43it/s]


0 大家好，我是沐柚，很高兴认识大家这个项目开源不到一周，star数量已经来到了十五K。


1 ChatTTS is optimized for dialogue,based tasks, enabling natural and expressive speech synthesis. It supports multiple speakers, facilitating interactive conversations. 


## LLM Call

In [25]:
from ChatTTS.experimental.llm import llm_api

API_KEY = 'sk-c0bce3336a214896810d78d34d9a99f9'
client = llm_api(api_key=API_KEY,
        base_url="https://api.deepseek.com",
        model="deepseek-chat")

In [28]:
rand_spk = chat.sample_random_speaker(seed=919)
user_question = '云南有哪些好吃的美食呢?'
text = client.call(user_question, prompt_version = 'deepseek')
print(text)
# text = client.call(text, prompt_version = 'deepseek_TN')
# print(text)

INFO:httpx:HTTP Request: POST https://api.deepseek.com/chat/completions "HTTP/1.1 200 OK"


云南美食丰富多样， 有著名的过桥米线， 酸辣可口的云南小煮， 香辣的云南火锅， 还有特色的云南米糕和鲜花饼。这些美食口味独特， 值得一试。


In [29]:
params_infer_code = {'spk_emb' : rand_spk, 'temperature':.3}

wav = chat.infer(text, params_infer_code=params_infer_code)

INFO:ChatTTS.core:All initialized.
 35%|███▌      | 721/2048 [00:15<00:28, 46.87it/s]


In [30]:
Audio(wav[0], rate=24_000, autoplay=False)